
# Random forest regression

We want to approximate a discipline with two inputs and two outputs:

- $y_1=1+2x_1+3x_2$
- $y_2=-1-2x_1-3x_2$

over the unit hypercube $[0,1]\times[0,1]$.


## Import



In [ ]:
from __future__ import annotations

from gemseo import configure_logger
from gemseo import create_design_space
from gemseo import create_discipline
from gemseo import create_scenario
from gemseo.mlearning import create_regression_model
from numpy import array

configure_logger()

## Create the discipline to learn
We can implement this analytic discipline by means of the
:class:`.AnalyticDiscipline` class.



In [ ]:
expressions = {"y_1": "1+2*x_1+3*x_2", "y_2": "-1-2*x_1-3*x_2"}
discipline = create_discipline(
    "AnalyticDiscipline", name="func", expressions=expressions
)

## Create the input sampling space
We create the input sampling space by adding the variables one by one.



In [ ]:
design_space = create_design_space()
design_space.add_variable("x_1", l_b=0.0, u_b=1.0)
design_space.add_variable("x_2", l_b=0.0, u_b=1.0)

## Create the learning set
We can build a learning set by means of a
:class:`.DOEScenario` with a full factorial design of
experiments. The number of samples can be equal to 9 for example.



In [ ]:
scenario = create_scenario(
    [discipline], "DisciplinaryOpt", "y_1", design_space, scenario_type="DOE"
)
scenario.execute({"algo": "fullfact", "n_samples": 9})

## Create the regression model
Then, we build the linear regression model from the database and
displays this model.



In [ ]:
dataset = scenario.to_dataset(opt_naming=False)
model = create_regression_model("RandomForestRegressor", data=dataset)
model.learn()
model

## Predict output
Once it is built, we can use it for prediction.



In [ ]:
input_value = {"x_1": array([1.0]), "x_2": array([2.0])}
output_value = model.predict(input_value)
output_value